#### 练习7. Naive RAG
1. 下载上市公司年报数据，数据要求
    1. 9家公司：3家上交所，3家港交所，3家美国上市公司
    2. 每一家上市公司至少过去连续3年的财报文件
2. Indexing：对文件进行读取，切片，向量化保存到向量库中
3. Retrieval & Generation：提出任意和年报有关的问题，能够精确的找出相关问题的片段并回答。问题至少包括以下几个方面
    1. 语义理解类型问题：xxxx公司xxxx年业绩主要的变化
    2. 指标提取类：xxxx年xx 公司
    3. 【可选】指标计算类：xxxx年xx公司的流动比率（Current Ratio）是多少？


In [68]:
import os
from dotenv import load_dotenv
from langchain_community.embeddings import JinaEmbeddings
from langchain_openai import ChatOpenAI
import weaviate
from langchain_weaviate import WeaviateVectorStore

load_dotenv()
os.environ["HF_ENDPOINT"] = "https://hf-mirror.com"
jina_api_key = os.getenv('JINA_API_KEY')
qwen_base_url = os.getenv('BAILIAN_API_BASE_URL')
qwen_api_key = os.getenv('BAILIAN_API_KEY')

embeddings = JinaEmbeddings(
    jina_api_key=jina_api_key,
    model_name="jina-embeddings-v4",
)

client = weaviate.connect_to_local()

data_dir = "data/年报"

# vectorstore = WeaviateVectorStore(
#     client=client,
#     index_name="AnnualReports",
#     text_key="content",
#     embedding=embeddings
# )

vectorstore = WeaviateVectorStore(
    client=client,
    index_name="AnnualReports_test7",
    text_key="text",
    embedding=embeddings
)

llm = ChatOpenAI(
    base_url=qwen_base_url,
    api_key=qwen_api_key,
    model="qwen3-30b-a3b",
    temperature=0.1,
    streaming=True
)

In [ ]:
from langchain.docstore.document import Document
from unstructured.partition.pdf import partition_pdf
from unstructured.chunking.title import chunk_by_title

def load_with_unstructured(file_path, metadata=None):
    """
    使用unstructured加载PDF文档，保持结构化内容
    """
    if metadata is None:
        metadata = {"source": file_path}
    
    try:
        # 使用unstructured处理PDF，保持表格结构
        elements = partition_pdf(
            filename=file_path,
            strategy="auto",
            infer_table_structure=True,  # 推断表格结构
            include_page_breaks=True,  # 包含页面分隔
            extract_images_in_pdf=False,  # 不提取图片
            languages=["eng", "chi_sim", "chi_tra"]  # 支持中英文
        )
        
        documents = []
        
        for element in elements:
            # 检查元素类型
            element_type = str(type(element)).split('.')[-1].replace("'>", "")
            
            # 获取元素内容
            content = str(element).strip()
            if not content:
                continue
            
            # 创建文档
            doc = Document(
                page_content=content,
                metadata={
                    **metadata,
                    "element_type": element_type,
                    "page_number": getattr(element, "metadata", {})["page_number"]
                }
            )
            documents.append(doc)
        
        return documents
        
    except Exception as e:
        print(f"使用unstructured处理文件时出错: {str(e)}")
        # 如果unstructured失败，降级使用PyPDF
        print(f"    尝试使用PyPDF作为备选方案...")
        return load_with_pypdf_fallback(file_path, metadata)

def load_with_pypdf_fallback(file_path, metadata=None):
    """
    当unstructured失败时的PyPDF备选方案
    """
    try:
        from langchain.document_loaders import PyPDFLoader
        
        loader = PyPDFLoader(file_path)
        documents = loader.load()
        
        processed_docs = []
        for doc in documents:
            doc.metadata.update(metadata or {})
            doc.metadata['element_type'] = 'text'  # PyPDF只能处理文本
            processed_docs.append(doc)
        
        print(f"    ✓ PyPDF备选方案成功处理")
        return processed_docs
        
    except Exception as e:
        print(f"    ❌ PyPDF备选方案也失败: {str(e)}")
        return []

def create_smart_chunks(documents, max_chunk_size=1000, chunk_overlap=200):
    """
    创建智能分块，确保表格完整性
    """
    chunked_docs = []
    
    for doc in documents:
        element_type = doc.metadata["element_type"]
        
        # 表格类型的文档保持完整，不进行分块
        if "Table" in element_type:
            chunked_docs.append(doc)
        else:
            # 对文本内容进行分块
            content = doc.page_content
            
            if len(content) <= max_chunk_size:
                chunked_docs.append(doc)
            else:
                # 按段落分割
                paragraphs = content.split('\n\n')
                current_chunk = ""
                
                for paragraph in paragraphs:
                    # 检查添加当前段落是否会超出大小限制
                    potential_chunk = current_chunk + "\n\n" + paragraph if current_chunk else paragraph
                    
                    if len(potential_chunk) <= max_chunk_size:
                        current_chunk = potential_chunk
                    else:
                        # 保存当前块
                        if current_chunk:
                            chunk_doc = Document(
                                page_content=current_chunk,
                                metadata=doc.metadata.copy()
                            )
                            chunked_docs.append(chunk_doc)
                        
                        # 开始新块
                        current_chunk = paragraph
                
                # 保存最后一块
                if current_chunk:
                    chunk_doc = Document(
                        page_content=current_chunk,
                        metadata=doc.metadata.copy()
                    )
                    chunked_docs.append(chunk_doc)
    
    return chunked_docs

def process_documents_with_unstructured(data_dir, vectorstore):
    """
    使用unstructured处理文档并索引到向量存储
    """
    total_chunks = 0
    successful_files = 0
    failed_files = 0
    
    for company_folder in os.listdir(data_dir):
        company_path = os.path.join(data_dir, company_folder)
        if os.path.isdir(company_path):
            print(f"\n正在处理：{company_folder} 的年报...")
            
            # 获取PDF文件
            pdf_files = [f for f in os.listdir(company_path) if f.endswith('.pdf')]
            
            for pdf_file in pdf_files:
                pdf_path = os.path.join(company_path, pdf_file)
                print(f"\n  加载文件：{pdf_file}")
                
                try:
                    # 使用unstructured加载文档
                    metadata = {
                        'company': company_folder,
                        'file': pdf_file
                    }
                    documents = load_with_unstructured(pdf_path, metadata)
                    
                    if not documents:
                        print(f"    ❌ 无法从文件 {pdf_file} 中提取内容")
                        failed_files += 1
                        continue
                    
                    # 创建智能分块
                    split_docs = create_smart_chunks(documents)
                    print(f"    分割成 {len(split_docs)} 个文本块（包含表格块）")
                    
                    # 统计表格和文本块数量
                    table_count = sum(1 for doc in split_docs if "Table" in doc.metadata["element_type"])
                    text_count = len(split_docs) - table_count
                    print(f"    - 表格块: {table_count} 个")
                    print(f"    - 文本块: {text_count} 个")
                    
                    # 添加到向量存储
                    print("    添加文档到向量存储...")
                    vectorstore.add_documents(split_docs)
                    
                    total_chunks += len(split_docs)
                    successful_files += 1
                    print(f"    ✓ 已处理完成，累计文本块数：{total_chunks}")
                    
                except Exception as e:
                    print(f"    ❌ 处理文件 {pdf_file} 时出错: {str(e)}")
                    failed_files += 1
                    continue
    
    print(f"\n🎉 所有文档处理完成！")
    print(f"📊 总计处理了 {total_chunks} 个文本块")
    print(f"✅ 成功处理 {successful_files} 个文件")
    print(f"❌ 失败 {failed_files} 个文件")
    print("✅ 所有文档已成功索引到 Weaviate!")

# 执行文档处理
process_documents_with_unstructured(data_dir, vectorstore)

In [69]:
# MinerU解析后json处理
import json
import os
from langchain.docstore.document import Document
from bs4 import BeautifulSoup
import pandas as pd
from io import StringIO

def extract_text_from_block(block):
    """从块中提取文本内容"""
    text_parts = []
    
    if 'lines' in block:
        for line in block['lines']:
            if 'spans' in line:
                for span in line['spans']:
                    if span.get('type') == 'text' and 'content' in span:
                        text_parts.append(span['content'])
    
    return ' '.join(text_parts).strip()

def extract_table_html_from_block(block):
    """从表格块中提取HTML内容"""
    if block.get('type') != 'table':
        return None
    
    # 在blocks -> lines -> spans中查找HTML
    blocks = block.get('blocks', [])
    for sub_block in blocks:
        lines = sub_block.get('lines', [])
        for line in lines:
            spans = line.get('spans', [])
            for span in spans:
                if span.get('type') == 'table' and 'html' in span:
                    return span['html']
    
    return None

def extract_table_text_with_pandas(table_html):
    """使用pandas从表格HTML中提取结构化文本内容"""
    if not table_html:
        return ""
    
    try:
        # 使用pandas读取HTML表格
        dfs = pd.read_html(StringIO(table_html))
        if not dfs:
            return ""
        
        # 获取第一个表格（通常只有一个）
        df = dfs[0]
        
        # 处理空值和清理数据
        df = df.fillna('')
        
        # 转换为更适合嵌入的文本格式
        table_text_parts = []
        
        # 添加列标题
        headers = [str(col) for col in df.columns if str(col) != 'nan']
        if headers:
            table_text_parts.append("表格列标题: " + " | ".join(headers))
        
        # 添加每一行数据
        for idx, row in df.iterrows():
            row_data = []
            for col_idx, value in enumerate(row):
                if str(value).strip() and str(value) != 'nan':
                    # 如果有列名，使用"列名: 值"的格式
                    if col_idx < len(headers) and headers[col_idx]:
                        row_data.append(f"{headers[col_idx]}: {value}")
                    else:
                        row_data.append(str(value))
            
            if row_data:
                table_text_parts.append(" | ".join(row_data))
        
        result = '\n'.join(table_text_parts)
        
        # 如果pandas处理失败，降级使用BeautifulSoup
        if not result.strip():
            return extract_table_text_fallback(table_html)
        
        return result
        
    except Exception as e:
        print(f"pandas表格解析错误，降级使用BeautifulSoup: {e}")
        return extract_table_text_fallback(table_html)

def extract_table_text_fallback(table_html):
    """当pandas失败时的BeautifulSoup备选方案"""
    if not table_html:
        return ""
    
    try:
        soup = BeautifulSoup(table_html, 'html.parser')
        table = soup.find('table')
        if not table:
            return ""
        
        rows = []
        for tr in table.find_all('tr'):
            cells = []
            for td in tr.find_all(['td', 'th']):
                cell_text = td.get_text(strip=True)
                if cell_text:
                    cells.append(cell_text)
            if cells:
                rows.append(' | '.join(cells))
        
        return '\n'.join(rows)
    except Exception as e:
        print(f"BeautifulSoup表格解析也失败: {e}")
        return ""

def extract_table_text(table_html):
    """优化版表格文本提取 - 简洁清晰的格式"""
    if not table_html:
        return ""
    
    try:
        # 使用pandas提取表格结构
        dfs = pd.read_html(StringIO(table_html))
        if dfs:
            df = dfs[0].fillna('')
            
            # 智能识别表格类型
            html_lower = table_html.lower()
            content_text = ' '.join([str(cell) for row in df.values for cell in row if pd.notna(cell)]).lower()
            
            # 识别表格类型
            table_type = ""
            if (any(term in html_lower for term in ['consolidated statements of operations', 'income statement', 'profit loss', 'earnings', '合并利润表', '利润表', '收益表']) or
                any(term in content_text for term in ['net sales', 'total net sales', 'net income', 'gross profit', 'operating income', 'revenue', '营业收入', '净利润', '营业利润', '利润总额', '基本每股收益'])):
                table_type = "合并利润表/损益表"
            
            elif (any(term in html_lower for term in ['balance sheet', 'financial position', 'statement of financial position', '合并资产负债表', '资产负债表', '财务状况表']) or
                  any(term in content_text for term in ['total assets', 'current assets', 'total liabilities', 'shareholders equity', '资产总计', '流动资产', '非流动资产', '负债总计', '股东权益', '所有者权益', '流动负债', '非流动负债'])):
                table_type = "合并资产负债表"
            
            elif (any(term in html_lower for term in ['cash flow', 'cash flows', '合并现金流量表', '现金流量表']) or
                  any(term in content_text for term in ['operating activities', 'investing activities', 'financing activities', '经营活动产生的现金流量', '投资活动产生的现金流量', '筹资活动产生的现金流量', '现金及现金等价物'])):
                table_type = "合并现金流量表"
            
            else:
                table_type = "财务数据表"
            
            # 生成结构化文本摘要
            table_rows = []
            for _, row in df.iterrows():
                row_data = []
                for col_idx, value in enumerate(row):
                    if pd.notna(value) and str(value).strip():
                        text = str(value).strip()
                        col_name = str(df.columns[col_idx]) if col_idx < len(df.columns) and str(df.columns[col_idx]) != 'nan' else ""
                        
                        # 只对重要的财务数据添加列名
                        if col_name and any(term in text.lower() for term in [
                            'assets', 'liabilities', 'equity', 'revenue', 'income', 'profit', 'cash',
                            '资产', '负债', '权益', '收入', '利润', '现金', '流动', '非流动'
                        ]):
                            row_data.append(f"{col_name}: {text}")
                        else:
                            row_data.append(text)
                
                if row_data:
                    table_rows.append(" | ".join(row_data))
            
            # 构建最终输出 - 更简洁的格式
            if table_type and table_rows:
                result = f"""[{table_type}]
{chr(10).join(table_rows[:10])}

{table_html.strip()}"""
            else:
                result = table_html.strip()
            
            return result
    
    except Exception as e:
        print(f"表格解析失败，使用原始HTML: {e}")
        return table_html.strip()
    
    return table_html.strip()

def extract_table_text_hybrid(table_html):
    """混合方案：HTML + 结构化摘要"""
    if not table_html:
        return ""
    
    # 1. 保留完整HTML（供展示）
    html_content = table_html.strip()
    
    # 2. 添加结构化文本摘要（供搜索）
    try:
        dfs = pd.read_html(StringIO(table_html))
        if dfs:
            df = dfs[0].fillna('')
            
            # 生成关键摘要
            summary_parts = ["=== 表格数据摘要 ==="]
            for _, row in df.iterrows():
                row_text = []
                for col, value in zip(df.columns, row):
                    if str(value).strip() and str(value) != 'nan':
                        row_text.append(f"{col}: {value}")
                if row_text:
                    summary_parts.append(" | ".join(row_text))
            
            summary = "\n".join(summary_parts)
            
            # 3. 组合：摘要 + HTML
            return f"{summary}\n\n=== 原始表格 ===\n{html_content}"
    except:
        pass
    
    return html_content

def process_mineru_json(json_file_path, metadata=None):
    """
    处理MinerU生成的JSON文件 - 改进版，解决表格分割问题
    
    Args:
        json_file_path: JSON文件路径
        metadata: 额外的元数据
    
    Returns:
        List[Document]: 处理后的文档列表
    """
    if metadata is None:
        metadata = {"source": json_file_path}
    
    try:
        with open(json_file_path, 'r', encoding='utf-8') as f:
            data = json.load(f)
        
        documents = []
        
        # 处理每一页
        for page_idx, page_info in enumerate(data.get('pdf_info', []), 1):
            para_blocks = page_info.get('para_blocks', [])
            
            # 找出所有表格块的位置
            table_blocks_info = []
            for i, block in enumerate(para_blocks):
                if block.get('type') == 'table':
                    table_blocks_info.append({'index': i, 'block': block})
            
            # 改进的表格合并逻辑
            processed_table_indices = set()
            
            for table_info in table_blocks_info:
                table_idx = table_info['index']
                if table_idx in processed_table_indices:
                    continue
                
                # 收集相邻的表格块（更激进的合并策略）
                related_tables = [table_info]
                related_indices = [table_idx]
                
                # 向前和向后查找相邻的表格块
                for other_table in table_blocks_info:
                    other_idx = other_table['index']
                    if other_idx != table_idx and other_idx not in processed_table_indices:
                        # 如果距离很近（8个块以内），尝试合并
                        if abs(other_idx - table_idx) <= 8:
                            # 检查是否是财务相关的表格
                            if is_financial_related_table(table_info['block'], other_table['block']):
                                related_tables.append(other_table)
                                related_indices.append(other_idx)
                
                # 标记这些表格为已处理
                processed_table_indices.update(related_indices)
                
                # 收集上下文标题
                title_blocks = []
                min_idx = min(related_indices)
                max_idx = max(related_indices)
                
                # 扩大搜索范围，查找更远的上下文
                for j in range(max(0, min_idx - 10), min_idx):
                    if j not in related_indices:
                        prev_block = para_blocks[j]
                        prev_text = extract_text_from_block(prev_block)
                        
                        # 更宽松的标题识别条件
                        if prev_text and len(prev_text) < 500:
                            if any(keyword in prev_text.lower() for keyword in [
                                'consolidated statements of operations', 'income statement', 
                                'statements of operations', 'operations', 'financial',
                                'consolidated', 'statements', 'apple', 'net sales', 'net income',
                                'table', 'statement', 'income', 'balance', 'cash', 'revenue', 
                                'years ended', 'comprehensive income', 'financial position',
                                '报表', '财务', '收益', '利润', '损益', '资产负债', '现金流'
                            ]):
                                title_blocks.insert(0, prev_text)
                
                # 构建合并的表格内容
                merged_content_parts = []
                
                # 添加标题
                if title_blocks:
                    merged_content_parts.extend(title_blocks)
                
                # 合并所有相关表格
                all_table_htmls = []
                all_table_texts = []
                
                for table_info in sorted(related_tables, key=lambda x: x['index']):
                    table_html = extract_table_html_from_block(table_info['block'])
                    if table_html:
                        all_table_htmls.append(table_html)
                        table_text = extract_table_text(table_html)
                        if table_text:
                            all_table_texts.append(table_text)
                    else:
                        # 如果没有HTML，尝试提取文本
                        table_text = extract_text_from_block(table_info['block'])
                        if table_text:
                            all_table_texts.append(table_text)
                
                # 如果有多个表格，创建一个综合的表格文档
                if all_table_texts:
                    if len(all_table_texts) > 1:
                        # 多表格合并 - 标记为merged类型
                        combined_text = "\n\n=== 合并表格内容 ===\n\n".join(all_table_texts)
                        merged_content_parts.append(combined_text)
                        element_type = "table_html_merged"
                    else:
                        # 单个表格
                        merged_content_parts.append(all_table_texts[0])
                        element_type = "table_html"
                    
                    if merged_content_parts:
                        table_doc = Document(
                            page_content='\n\n'.join(merged_content_parts),
                            metadata={
                                **metadata,
                                "page_number": page_idx,
                                "element_type": element_type,
                                "block_indices": related_indices,
                                "table_count": len(related_tables)
                            }
                        )
                        documents.append(table_doc)
            
            # 处理非表格内容（保持原有逻辑）
            current_chunk = []
            current_chunk_size = 0
            max_chunk_size = 1000
            min_chunk_size = 100
            
            for i, block in enumerate(para_blocks):
                if block.get('type') != 'table':  # 跳过表格块
                    text_content = extract_text_from_block(block)
                    if text_content:
                        if current_chunk_size + len(text_content) > max_chunk_size and current_chunk:
                            chunk_content = '\n\n'.join(current_chunk)
                            if len(chunk_content) >= min_chunk_size:
                                chunk_doc = Document(
                                    page_content=chunk_content,
                                    metadata={
                                        **metadata,
                                        "page_number": page_idx,
                                        "element_type": "text"
                                    }
                                )
                                documents.append(chunk_doc)
                            current_chunk = [text_content]
                            current_chunk_size = len(text_content)
                        else:
                            current_chunk.append(text_content)
                            current_chunk_size += len(text_content)
            
            # 处理页面结束时剩余的chunk
            if current_chunk:
                chunk_content = '\n\n'.join(current_chunk)
                if len(chunk_content) >= min_chunk_size:
                    chunk_doc = Document(
                        page_content=chunk_content,
                        metadata={
                            **metadata,
                            "page_number": page_idx,
                            "element_type": "text"
                        }
                    )
                    documents.append(chunk_doc)
        
        return documents
        
    except Exception as e:
        print(f"处理JSON文件时出错: {e}")
        return []

def is_financial_related_table(block1, block2):
    """
    检查两个表格块是否是相关的财务表格
    """
    # 提取两个表格的HTML内容
    html1 = extract_table_html_from_block(block1)
    html2 = extract_table_html_from_block(block2)
    
    if not html1 or not html2:
        return False
    
    financial_keywords = [
        'net sales', 'total net sales', 'revenue', 'income', 'profit', 'loss',
        'operating', 'gross', 'expenses', 'cost', '$', 'million', 'billion',
        'consolidated', 'statements', 'operations',
        '营业收入', '营业利润', '利润总额', '净利润', '人民币', '百万元', '千元',
        '资产', '负债', '权益', '现金流量', '合并', '报表', '财务',
        '通信服务收入', '销售产品收入', '网络运营', '折旧', '摊销',
        '流动资产', '非流动资产', '流动负债', '股东权益', '每股收益'
    ]
    
    html1_lower = html1.lower()
    html2_lower = html2.lower()
    
    # 计算每个表格包含的财务关键词数量
    count1 = sum(1 for kw in financial_keywords if kw in html1_lower)
    count2 = sum(1 for kw in financial_keywords if kw in html2_lower)
    
    # 如果都包含足够的财务关键词，认为是相关的
    return count1 >= 2 and count2 >= 2

def process_mineru_directory(data_dir, vectorstore, skip_files=None, batch_size=100):
    """
    处理包含MinerU JSON文件的目录
    
    Args:
        data_dir: 数据目录路径
        vectorstore: 向量存储实例
        skip_files: 要跳过的文件列表 (默认为None)
        batch_size: 批处理大小，避免超过向量化限制 (默认100)
    """
    if skip_files is None:
        skip_files = []
    
    total_chunks = 0
    successful_files = 0
    failed_files = 0
    processed_files = []
    
    for company_folder in os.listdir(data_dir):
        company_path = os.path.join(data_dir, company_folder)
        if os.path.isdir(company_path):
            print(f"\n正在处理：{company_folder} 的年报...")
            
            # 获取JSON文件
            json_files = [f for f in os.listdir(company_path) if f.endswith('.json')]
            
            for json_file in json_files:
                # 检查是否需要跳过此文件
                if json_file in skip_files:
                    print(f"\n  ⏭️  跳过文件：{json_file}")
                    continue
                
                json_path = os.path.join(company_path, json_file)
                print(f"\n  加载文件：{json_file}")
                
                try:
                    # 验证JSON文件格式
                    with open(json_path, 'r', encoding='utf-8') as f:
                        test_data = json.load(f)
                    
                    # 处理JSON文件
                    metadata = {
                        'company': company_folder,
                        'file': json_file.replace('.json', '.pdf')  # 假设JSON对应PDF
                    }
                    documents = process_mineru_json(json_path, metadata)
                    
                    if not documents:
                        print(f"    ❌ 无法从文件 {json_file} 中提取内容")
                        failed_files += 1
                        continue
                    
                    print(f"    提取到 {len(documents)} 个文档块")
                    
                    # 统计表格和文本块数量
                    table_count = sum(1 for doc in documents if doc.metadata.get("element_type") == "table_html")
                    text_count = len(documents) - table_count
                    print(f"    - HTML表格块: {table_count} 个")
                    print(f"    - 文本块: {text_count} 个")
                    
                    # 分批添加到向量存储，避免超过512项限制
                    print(f"    分批添加文档到向量存储（批大小: {batch_size}）...")
                    for i in range(0, len(documents), batch_size):
                        batch = documents[i:i + batch_size]
                        try:
                            vectorstore.add_documents(batch)
                            print(f"      ✓ 已处理批次 {i//batch_size + 1}/{(len(documents)-1)//batch_size + 1}")
                        except Exception as batch_error:
                            print(f"      ❌ 批次 {i//batch_size + 1} 处理失败: {str(batch_error)}")
                            # 如果批处理失败，尝试单个处理
                            print(f"      🔄 尝试单个文档处理...")
                            for doc in batch:
                                try:
                                    vectorstore.add_documents([doc])
                                except Exception as single_error:
                                    print(f"        ❌ 单个文档处理失败: {str(single_error)}")
                                    continue
                    
                    total_chunks += len(documents)
                    successful_files += 1
                    processed_files.append(json_file)
                    print(f"    ✓ 已处理完成，累计文本块数：{total_chunks}")
                    
                except json.JSONDecodeError as je:
                    print(f"    ❌ JSON格式错误 {json_file}: {str(je)}")
                    print(f"      建议检查文件是否完整或重新生成")
                    failed_files += 1
                    continue
                except Exception as e:
                    error_msg = str(e)
                    if "512 items" in error_msg:
                        print(f"    ❌ 文档数量超限 {json_file}: 尝试减小batch_size")
                    elif "Internal server error" in error_msg:
                        print(f"    ❌ 服务器错误 {json_file}: 建议稍后重试")
                    else:
                        print(f"    ❌ 处理文件 {json_file} 时出错: {error_msg}")
                    failed_files += 1
                    continue
    
    print(f"\n🎉 所有JSON文档处理完成！")
    print(f"📊 总计处理了 {total_chunks} 个文本块")
    print(f"✅ 成功处理 {successful_files} 个文件")
    print(f"❌ 失败 {failed_files} 个文件")
    
    if processed_files:
        print(f"\n✅ 成功处理的文件:")
        for pf in processed_files:
            print(f"  - {pf}")
    
    if failed_files > 0:
        print(f"\n⚠️  失败文件处理建议:")
        print(f"  - JSON格式错误：检查文件完整性，重新生成MinerU解析")
        print(f"  - 512项限制：使用更小的batch_size参数")
        print(f"  - 服务器错误：稍后重试，或检查网络连接")
        print(f"  - 使用skip_files参数跳过已处理的文件")
    
    print("✅ 所有文档已成功索引到 Weaviate!")
    
    return {
        'total_chunks': total_chunks,
        'successful_files': successful_files,
        'failed_files': failed_files,
        'processed_files': processed_files
    }

def retry_failed_files(data_dir, vectorstore, failed_files, batch_size=30):
    """
    专门重试失败的文件
    """
    print(f"🔄 重试 {len(failed_files)} 个失败的文件...")
    
    for failed_file in failed_files:
        print(f"\n🎯 重试处理: {failed_file}")
        
        # 查找文件所在的公司文件夹
        found = False
        for company_folder in os.listdir(data_dir):
            company_path = os.path.join(data_dir, company_folder)
            if os.path.isdir(company_path):
                json_path = os.path.join(company_path, failed_file)
                if os.path.exists(json_path):
                    found = True
                    print(f"  📁 在 {company_folder} 中找到文件")
                    
                    try:
                        # 验证JSON格式
                        with open(json_path, 'r', encoding='utf-8') as f:
                            data = json.load(f)
                        
                        # 处理文件
                        metadata = {
                            'company': company_folder,
                            'file': failed_file.replace('.json', '.pdf')
                        }
                        documents = process_mineru_json(json_path, metadata)
                        
                        if documents:
                            print(f"    ✅ 提取到 {len(documents)} 个文档块")
                            
                            # 超小批次处理
                            for i in range(0, len(documents), batch_size):
                                batch = documents[i:i + batch_size]
                                try:
                                    vectorstore.add_documents(batch)
                                    print(f"      ✓ 批次 {i//batch_size + 1} 处理成功")
                                except Exception as e:
                                    print(f"      ❌ 批次失败: {str(e)}")
                                    # 逐个处理
                                    for doc in batch:
                                        try:
                                            vectorstore.add_documents([doc])
                                        except:
                                            continue
                            
                            print(f"    ✅ {failed_file} 重试成功!")
                        else:
                            print(f"    ❌ {failed_file} 无法提取内容")
                            
                    except json.JSONDecodeError:
                        print(f"    ❌ {failed_file} JSON格式错误，建议重新生成")
                    except Exception as e:
                        print(f"    ❌ {failed_file} 重试失败: {str(e)}")
                    
                    break
        
        if not found:
            print(f"  ❌ 未找到文件: {failed_file}")

# 如果您有MinerU JSON文件，请使用以下代码处理
# process_mineru_directory("data/年报_json", vectorstore)

print("MinerU JSON处理函数已定义完成")

MinerU JSON处理函数已定义完成


In [70]:
skip_successful_files = []

# 定义失败的文件，可以单独重试
failed_files_to_retry = [
    '中国移动：2024年度报告.json',
    '腾讯音乐-SW：2022年度报告.json',
    '腾讯音乐-SW：2023年度报告.json', 
    '腾讯音乐-SW：2024年度报告.json'
]

# 处理失败的文件，使用更小的批处理大小
result = process_mineru_directory(
    data_dir, 
    vectorstore, 
    skip_files=skip_successful_files,  # 跳过已成功处理的文件
    batch_size=50  # 使用更小的批处理大小，避免512项限制
)

print(f"\n📋 处理结果总结:")
print(f"✅ 本次成功: {result['successful_files']} 个文件")
print(f"❌ 本次失败: {result['failed_files']} 个文件") 
print(f"📊 本次新增: {result['total_chunks']} 个文档块")


正在处理：中国移动（A股）[600941] 的年报...

  加载文件：中国移动：2023年度报告.json
    提取到 420 个文档块
    - HTML表格块: 194 个
    - 文本块: 226 个
    分批添加文档到向量存储（批大小: 50）...
    提取到 420 个文档块
    - HTML表格块: 194 个
    - 文本块: 226 个
    分批添加文档到向量存储（批大小: 50）...
      ❌ 批次 1 处理失败: HTTPSConnectionPool(host='api.jina.ai', port=443): Max retries exceeded with url: /v1/embeddings (Caused by SSLError(SSLEOFError(8, '[SSL: UNEXPECTED_EOF_WHILE_READING] EOF occurred in violation of protocol (_ssl.c:1016)')))
      🔄 尝试单个文档处理...
      ❌ 批次 1 处理失败: HTTPSConnectionPool(host='api.jina.ai', port=443): Max retries exceeded with url: /v1/embeddings (Caused by SSLError(SSLEOFError(8, '[SSL: UNEXPECTED_EOF_WHILE_READING] EOF occurred in violation of protocol (_ssl.c:1016)')))
      🔄 尝试单个文档处理...
      ✓ 已处理批次 2/9
      ✓ 已处理批次 2/9
      ✓ 已处理批次 3/9
      ✓ 已处理批次 3/9
      ✓ 已处理批次 4/9
      ✓ 已处理批次 4/9
      ✓ 已处理批次 5/9
      ✓ 已处理批次 5/9
      ✓ 已处理批次 6/9
      ✓ 已处理批次 6/9
      ✓ 已处理批次 7/9
      ✓ 已处理批次 7/9
      ✓ 已处理批次 8/9
      ✓ 已处理批次 8

In [11]:
retry_failed_files(data_dir, vectorstore, failed_files_to_retry, batch_size=30)

🔄 重试 4 个失败的文件...

🎯 重试处理: 中国移动：2024年度报告.json
  📁 在 中国移动（A股）[600941] 中找到文件
    ✅ 提取到 439 个文档块
    ✅ 提取到 439 个文档块
      ✓ 批次 1 处理成功
      ✓ 批次 1 处理成功
      ✓ 批次 2 处理成功
      ✓ 批次 2 处理成功
      ✓ 批次 3 处理成功
      ✓ 批次 3 处理成功
      ✓ 批次 4 处理成功
      ✓ 批次 4 处理成功
      ✓ 批次 5 处理成功
      ✓ 批次 5 处理成功
      ✓ 批次 6 处理成功
      ✓ 批次 6 处理成功
      ✓ 批次 7 处理成功
      ✓ 批次 7 处理成功
      ✓ 批次 8 处理成功
      ✓ 批次 8 处理成功
      ✓ 批次 9 处理成功
      ✓ 批次 9 处理成功
      ✓ 批次 10 处理成功
      ✓ 批次 10 处理成功
      ✓ 批次 11 处理成功
      ✓ 批次 11 处理成功
      ✓ 批次 12 处理成功
      ✓ 批次 12 处理成功
      ✓ 批次 13 处理成功
      ✓ 批次 13 处理成功
      ✓ 批次 14 处理成功
      ✓ 批次 14 处理成功
      ✓ 批次 15 处理成功
    ✅ 中国移动：2024年度报告.json 重试成功!

🎯 重试处理: 腾讯音乐-SW：2022年度报告.json
  📁 在 腾讯音乐-SW（港股）[01698] 中找到文件
      ✓ 批次 15 处理成功
    ✅ 中国移动：2024年度报告.json 重试成功!

🎯 重试处理: 腾讯音乐-SW：2022年度报告.json
  📁 在 腾讯音乐-SW（港股）[01698] 中找到文件
    ✅ 提取到 513 个文档块
    ✅ 提取到 513 个文档块
      ✓ 批次 1 处理成功
      ✓ 批次 1 处理成功
      ✓ 批次 2 处理成功
      ✓ 批次 2 处理成功
      ✓ 批次 3 处理成功
      ✓ 批次 3 处理成功
    

In [7]:
client.close()

In [6]:
def query_vector_collection(client: weaviate.WeaviateClient, collection_name: str, query: str, k: int) -> list:
    """
    从集合中查询数据
    :param client: Weaviate 客户端
    :param collection_name: 集合名称
    :param query: 查询的【向量】
    :param k: 返回的结果数量
    :return: 查询结果列表
    """
    
    collection = client.collections.get(collection_name)
    response = collection.query.hybrid(
        query=query,
        vector=embeddings.embed_query(query)
    )
    documents = [res.properties['text'] for res in response.objects]
    return documents

result = query_vector_collection(client, "AnnualReports_test3", query="2023 Apple CONSOLIDATED STATEMENTS OF OPERATIONS 表格", k=5)
print("result: ", result)

result:  ['Report of Independent Registered Public Accounting Firm\n\nTo the Shareholders and the Board of Directors of Apple Inc.\n\nOpinion on the Financial Statements\n\nWe have audited the accompanying consolidated balance sheets of Apple Inc. as of September 30, 2023 and September 24, 2022, the related consolidated statements of operations, comprehensive income, shareholders\' equity and cash flows for each of the three years in the period ended September 30, 2023, and the related notes (collectively referred to as the "financial statements"). In our opinion, the financial statements present fairly, in all material respects, the financial position of Apple Inc. at September 30, 2023 and September 24, 2022, and the results of its operations and its cash flows for each of the three years in the period ended September 30, 2023, in conformity with U.S. generally accepted accounting principles.', "Apple Inc.\n\nNotes to Consolidated Financial Statements\n\nNote 1 - Summary of Significa

In [44]:
from langchain.chains import RetrievalQA
from langchain.prompts import PromptTemplate

retriever = vectorstore.as_retriever(
    search_type="mmr",
    search_kwargs={"k": 7, "lambda_mult": 0.85}
)

prompt_template = """
你是一名资深专业财务分析师、股票分析师和金融投资专家。你将看到来自上市公司发布的年度报告中相关的文档片段。
基于以下相关文档片段，请准确回答用户的问题。如果文档中没有足够信息回答问题，请说明缺少相关信息。
请根据文档片段的元数据确定该片段属于哪个公司、什么年份，如果提供的文档片段与问题中指定的公司或年份不相关，请不要使用该片段回答问题。

相关文档:
{context}

问题: {question}

请提供详细和准确的答案，并给出相关的文档片段作为支持依据。请确保答案是基于提供的文档内容，而不是外部知识或假设。:
"""

PROMPT = PromptTemplate(
    template=prompt_template,
    input_variables=["context", "question"]
)

# Create RetrievalQA chain
qa_chain = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=retriever,
    chain_type_kwargs={"prompt": PROMPT},
    return_source_documents=True
)

def ask_question(question):
    print(f"\n问题: {question}")
    print("-" * 80)
    
    result = qa_chain({"query": question})
    
    print(f"答案: {result['result']}")
    print(f"\n相关文档片段数量: {len(result['source_documents'])}")
    
    # Show source documents
    for i, doc in enumerate(result['source_documents'][:3]):  # Show top 3 sources
        print(f"\n来源 {i+1}:")
        print(f"公司: {doc.metadata.get('company', 'Unknown')}")
        print(f"文件: {doc.metadata.get('file', 'Unknown')}")
        print(f"内容片段: {doc.page_content[:200]}...")
    
    return result

d:\yusys\202507\ai_learning\.venv\Lib\site-packages\weaviate\warnings.py:292: ResourceWarning: Con004: The connection to Weaviate was not closed properly. This can lead to memory leaks.
            Please make sure to close the connection using `client.close()`.
  warnings.warn(
C:\Users\ASUS\AppData\Local\Temp\ipykernel_27156\3473560771.py:4: ResourceWarning: unclosed <socket.socket fd=4720, family=2, type=1, proto=0, laddr=('127.0.0.1', 11457), raddr=('127.0.0.1', 8080)>
  retriever = vectorstore.as_retriever(


In [50]:
# 改进的问答系统 - 带公司过滤功能
from langchain.chains import RetrievalQA
from langchain.prompts import PromptTemplate

def ask_question_with_company_filter(question, target_company=None, k=8):
    """
    带公司过滤的问答函数，在检索阶段就过滤公司文档
    
    Args:
        question: 用户问题
        target_company: 目标公司名称（可选，如"Apple"、"中国移动"等）
        k: 最终返回的文档数量
    """
    print(f"\n问题: {question}")
    if target_company:
        print(f"🎯 目标公司: {target_company}")
    print("-" * 80)
    
    # 检查问题中是否明确提到表格
    def check_table_keywords(question):
        """检查问题中是否包含表格相关关键词"""
        table_keywords = [
            "表格", "表", "table", 
            "利润表", "损益表", "资产负债表", "现金流量表", "财务报表",
            "income statement", "balance sheet", "cash flow", "financial statement",
            "consolidated statements", "operations", "合并报表",
            "合并利润表", "合并资产负债表", "合并现金流量表", "合并股东权益变动表",
            "母公司利润表", "母公司资产负债表", "母公司现金流量表"
        ]
        question_lower = question.lower()
        found_keywords = [kw for kw in table_keywords if kw in question_lower]
        return len(found_keywords) > 0, found_keywords
    
    # 定义公司关键词
    def get_company_keywords(company):
        if not company:
            return []
        
        keywords = [company.lower()]
        if "apple" in company.lower():
            keywords.extend(["apple", "aapl", "苹果"])
        elif "中国移动" in company:
            keywords.extend(["中国移动", "china mobile", "600941", "中国移动通信", "移动通信", "中国移动有限公司", "china mobile limited"])
        elif "中国石油" in company:
            keywords.extend(["中国石油", "petro", "601857"])
        elif "腾讯" in company:
            keywords.extend(["腾讯", "tencent", "tme"])
        
        return keywords
    
    # 过滤文档的函数
    def filter_documents_by_company_and_type(docs, target_company, prefer_tables=False):
        if not target_company:
            company_filtered = docs
        else:
            company_keywords = get_company_keywords(target_company)
            company_filtered = []
            other_company_docs = []
            
            for doc in docs:
                company_name = doc.metadata.get('company', '').lower()
                file_name = doc.metadata.get('file', '').lower()
                
                # 检查是否匹配目标公司
                is_match = any(keyword in company_name or keyword in file_name 
                              for keyword in company_keywords)
                
                if is_match:
                    company_filtered.append(doc)
                else:
                    other_company_docs.append(doc)
        
        # 如果问题明确提到表格，优先筛选表格文档
        if prefer_tables:
            table_docs = []
            text_docs = []
            
            for doc in company_filtered:
                element_type = doc.metadata.get('element_type', '').lower()
                if 'table' in element_type:
                    table_docs.append(doc)
                else:
                    text_docs.append(doc)
            
            print(f"📋 表格类型筛选:")
            print(f"  - 表格文档: {len(table_docs)} 个")
            print(f"  - 文本文档: {len(text_docs)} 个")
            
            # 优先使用表格文档，如果数量不足再补充文本文档
            if table_docs:
                # 优先返回表格文档，如果不够k个再加入文本文档
                filtered_docs = table_docs + text_docs
                print(f"  ✅ 优先使用表格文档")
            else:
                filtered_docs = company_filtered
                print(f"  ⚠️  未找到表格文档，使用所有文档")
        else:
            filtered_docs = company_filtered
        
        # 打印过滤统计
        print(f"📊 检索过滤统计:")
        print(f"  - 总检索文档: {len(docs)}")
        if target_company:
            print(f"  - 匹配 {target_company}: {len(company_filtered)}")
            if 'other_company_docs' in locals():
                print(f"  - 过滤掉其他公司: {len(other_company_docs)}")
        print(f"  - 最终文档: {len(filtered_docs)}")
        
        return filtered_docs
    
    # 检查是否需要优先筛选表格
    is_table_question, table_keywords = check_table_keywords(question)
    if is_table_question:
        print(f"📋 检测到表格相关问题，关键词: {table_keywords}")
        print(f"✅ 将优先筛选表格类型文档")
    
    # 先进行向量检索，检索更多文档以提高命中率
    retriever = vectorstore.as_retriever(
        search_type="mmr",
        search_kwargs={"k": max(k * 3, 20), "lambda_mult": 0.85}  # 检索更多文档
    )
    
    # 获取原始检索结果
    docs = retriever.get_relevant_documents(question)
    
    # 过滤文档（公司 + 表格类型）
    filtered_docs = filter_documents_by_company_and_type(docs, target_company, is_table_question)
    
    # 检查过滤结果
    if target_company and len(filtered_docs) == 0:
        print(f"\n❌ 未找到 {target_company} 的相关文档")
        print("建议：")
        print("1. 检查公司名称是否正确")
        print("2. 尝试使用公司的其他称呼")
        print("3. 确认该公司数据是否已被索引")
        return {
            'result': f"未找到 {target_company} 的相关财务数据。请检查公司名称或确认数据是否已被索引。",
            'source_documents': []
        }
    elif target_company and len(filtered_docs) < 3:
        print(f"\n⚠️  仅找到 {len(filtered_docs)} 个相关文档，结果可能不够全面")
    
    # 限制最终文档数量
    final_docs = filtered_docs[:k]
    
    enhanced_prompt = """
你是一名资深专业财务分析师、股票分析师和金融投资专家。你将看到来自上市公司发布的年度报告中相关的文档片段。

基于以下相关文档片段，请准确回答用户的问题。如果文档中没有足够信息回答问题，请说明缺少相关信息。

特别注意：
- 对于中国移动等中国公司，重点关注合并利润表、合并资产负债表、合并现金流量表
- 识别中文财务术语如：营业收入、净利润、归属于母公司股东的净利润、基本每股收益等
- 金额单位通常为人民币百万元或千元，请注意单位转换
- 通信行业特有指标如：通信服务收入、网络运营成本、用户数等

相关文档:
{context}

问题: {question}

请提供详细和准确的答案，并给出相关的文档片段作为支持依据。请确保答案是基于提供的文档内容，而不是外部知识或假设。对于财务数据，请明确标注金额单位。
"""
    
    ENHANCED_PROMPT = PromptTemplate(
        template=enhanced_prompt,
        input_variables=["context", "question"]
    )
    
    # 手动构建上下文
    context = "\n\n".join([f"文档 {i+1}:\n{doc.page_content}" for i, doc in enumerate(final_docs)])
    
    # 直接调用LLM
    formatted_prompt = ENHANCED_PROMPT.format(context=context, question=question)
    response = llm.invoke(formatted_prompt)
    
    # 构建返回结果
    result = {
        'result': response.content,
        'source_documents': final_docs
    }
    
    print(f"\n答案: {result['result']}")
    print(f"\n📄 最终使用文档数量: {len(final_docs)}")
    
    # 显示源文档
    for i, doc in enumerate(final_docs[:3]):  # Show top 3 sources
        print(f"\n来源 {i+1}:")
        print(f"  公司: {doc.metadata.get('company', 'Unknown')}")
        print(f"  文件: {doc.metadata.get('file', 'Unknown')}")
        print(f"  类型: {doc.metadata.get('element_type', 'Unknown')}")
        print(f"  内容: {doc.page_content[:150]}...")
    
    return result

# 测试改进的问答系统 - 专门针对中国移动优化
print("🚀 针对中国移动优化的问答系统已就绪！")
print("使用方法：ask_question_with_company_filter('问题', '中国移动')")
print("例如：ask_question_with_company_filter('中国移动2023年营业收入是多少？', '中国移动')")
print("支持的财务报表类型：合并利润表、合并资产负债表、合并现金流量表、合并股东权益变动表")

🚀 针对中国移动优化的问答系统已就绪！
使用方法：ask_question_with_company_filter('问题', '中国移动')
例如：ask_question_with_company_filter('中国移动2023年营业收入是多少？', '中国移动')
支持的财务报表类型：合并利润表、合并资产负债表、合并现金流量表、合并股东权益变动表


In [ ]:
question = "中国移动公司2022年业绩主要的变化是什么？"

ask_question(question)
print("\n" + "="*100 + "\n")


问题: 中国移动公司2022年业绩主要的变化是什么？
--------------------------------------------------------------------------------
答案: 根据提供的文档片段，中国移动有限公司2022年业绩的主要变化可归纳如下：

### 1. **营业收入**
   - **数据**：2022年，中国移动的营业收入达到人民币**9,372.59亿元**。
   - **依据**：文档明确提到“2022年，营业收入达到人民币9,372.59亿元。”
   - **分析**：这是2022年业绩的核心财务指标，但文档未提供2021年同期数据，因此无法判断具体增长或下降幅度。

### 2. **客户规模**
   - **移动客户**：截至2022年底，移动客户总数达到**9.75亿户**。
   - **有线宽带客户**：有线宽带客户总数达到**2.72亿户**。
   - **依据**：文档提到“截至2022年12月31日，移动客户总数达到9.75亿户，有线宽带客户总数达到2.72亿户。”
   - **分析**：客户数量的庞大基数反映了公司在通信服务领域的市场渗透率，但同样缺乏历史数据对比。

### 3. **战略转型与业务布局**
   - **新型信息基础设施**：公司持续推动5G、算力网络、能力中台等新型信息基础设施建设。
   - **新型信息服务体系**：创新构建“连接+算力+能力”服务体系，覆盖生产、生活、治理全场景的数智化需求。
   - **依据**：文档提到“系统打造以5G、算力网络、能力中台为重点的新型信息基础设施……创新构建‘连接+算力+能力’新型信息服务体系”。
   - **分析**：这一战略调整可能带来长期业绩增长点，但属于业务结构优化，需结合后续财务数据验证效果。

### 4. **品牌与信用评级**
   - **品牌价值**：2022年，“中国移动”品牌位列Millward Brown“BrandZ™全球最具价值品牌100强”第88位。
   - **信用评级**：债信评级保持与中国国家主权评级一致，为标普A+/前景稳定和穆迪A1/前景稳定。
   - **依据**：文档提到“‘中国移动’品牌在2022年再次荣登Millward Brown的‘BrandZ™

![](https://rean-blog-bucket.oss-cn-guangzhou.aliyuncs.com/assets/essay/20250801101608.png)

In [45]:
question = "与2022年比较，中国移动公司2023年业绩主要的变化是什么？"

ask_question(question)
print("\n" + "="*100 + "\n")


问题: 与2022年比较，中国移动公司2023年业绩主要的变化是什么？
--------------------------------------------------------------------------------


C:\Users\ASUS\AppData\Local\Temp\ipykernel_27156\3473560771.py:40: LangChainDeprecationWarning: The method `Chain.__call__` was deprecated in langchain 0.1.0 and will be removed in 1.0. Use :meth:`~invoke` instead.
  result = qa_chain({"query": question})


答案: 根据提供的文档片段，该内容属于苹果公司（Apple Inc.）2024年年度报告（Form 10-K）中的“Management's Discussion and Analysis of Financial Condition and Results of Operations”部分，而非中国移动公司。文档中未提及任何关于“中国移动公司”的财务数据或业绩信息，因此无法回答该问题。

**关键依据：**
1. **公司身份**：文档中提到的产品（如MacBook Pro、iMac）和财务分析（如毛利率、研发费用）均指向苹果公司，而非中国移动。
2. **地理区域描述**：文档中提到的“Greater China”（大中华区）是苹果公司对中国的市场划分，但并未涉及中国移动公司的具体业绩。
3. **财务数据范围**：文档中的财务数据（如2023年运营费用、各地区净销售额）均属于苹果公司，未包含中国移动公司的任何信息。

**结论**：  
提供的文档片段与“中国移动公司”无关，因此无法基于此回答问题。若需分析中国移动公司的业绩变化，需提供其对应的财务报告数据。

相关文档片段数量: 7

来源 1:
公司: Apple Inc.（美股）[AAPL]
文件: aapl-20240928-10-K.pdf
内容片段: Item 7. Management's Discussion and Analysis of Financial Condition and Results of Operations

The following discussion should be read in conjunction with the consolidated financial statements and acc...

来源 2:
公司: Apple Inc.（美股）[AAPL]
文件: aapl-20240928-10-K.pdf
内容片段: The Company's future gross margins can be impacted by a variety of factors, as discussed in Part I, item 1A of this Form 10- K under the heading "Risk Factors." As

![](https://rean-blog-bucket.oss-cn-guangzhou.aliyuncs.com/assets/essay/20250801102549.png)

In [19]:
question = "从利润表上看，中国石油2023年的总收入、净利润分別是多少？"

ask_question(question)


问题: 从利润表上看，中国石油2023年的总收入、净利润分別是多少？
--------------------------------------------------------------------------------
答案: 根据中国石油天然气股份有限公司2023年度财务报表附注中的**合并综合收益表**，2023年的总收入和净利润如下：

### **总收入（营业收入）**  
**3,011,012 百万元**  
**依据文档片段**：  
在“合并综合收益表”中，营业收入（“营业收入”行）明确列示为 **3,011,012 人民币百万元**（2023年数据）。  
> 文档原文：  
> **营业收入  6  3,011,012  3,239,167**

---

### **净利润**  
**180,293 百万元**  
**依据文档片段**：  
在“合并综合收益表”中，净利润（“净利润”行）明确列示为 **180,293 人民币百万元**（2023年数据）。  
> 文档原文：  
> **净利润    180,293  163,348**

---

### **补充说明**  
1. **总收入的构成**：  
   根据附注中的“营业收入”分类，总收入由油气和新能源、炼油化工和新材料、销售、天然气销售等业务板块构成，合计为 **3,011,012 百万元**（见文档中“营业收入”部分的分项数据及合计数）。  

2. **净利润的计算逻辑**：  
   净利润是通过税前利润（237,462 百万元）减去所得税费用（57,169 百万元）得出，最终结果为 **180,293 百万元**。  

以上数据均直接来源于提供的财务报表附注，未涉及外部假设或计算。

相关文档片段数量: 5

来源 1:
公司: 中国石油（A股）[601857]
文件: 中国石油：2023年度报告.pdf
内容片段: 中国石油天然气股份有限公司 
2023 年度财务报表附注 
(除特别注明外，金额单位为人民币百万元) 
 
- 116 - 
1 公司简介 
 
中国石油天然气股份有限公司 (“本公司”)是由中国石油天然气集团公司根据
中华人民共和国(“中国”)原国家经济贸易委员会 《关于同意设立中国石油天然气股
份有限公司的复函》(国经贸企改[199

{'query': '从利润表上看，中国石油2023年的总收入、净利润分別是多少？',
 'result': '根据中国石油天然气股份有限公司2023年度财务报表附注中的**合并综合收益表**，2023年的总收入和净利润如下：\n\n### **总收入（营业收入）**  \n**3,011,012 百万元**  \n**依据文档片段**：  \n在“合并综合收益表”中，营业收入（“营业收入”行）明确列示为 **3,011,012 人民币百万元**（2023年数据）。  \n> 文档原文：  \n> **营业收入  6  3,011,012  3,239,167**\n\n---\n\n### **净利润**  \n**180,293 百万元**  \n**依据文档片段**：  \n在“合并综合收益表”中，净利润（“净利润”行）明确列示为 **180,293 人民币百万元**（2023年数据）。  \n> 文档原文：  \n> **净利润    180,293  163,348**\n\n---\n\n### **补充说明**  \n1. **总收入的构成**：  \n   根据附注中的“营业收入”分类，总收入由油气和新能源、炼油化工和新材料、销售、天然气销售等业务板块构成，合计为 **3,011,012 百万元**（见文档中“营业收入”部分的分项数据及合计数）。  \n\n2. **净利润的计算逻辑**：  \n   净利润是通过税前利润（237,462 百万元）减去所得税费用（57,169 百万元）得出，最终结果为 **180,293 百万元**。  \n\n以上数据均直接来源于提供的财务报表附注，未涉及外部假设或计算。',
 'source_documents': [Document(metadata={'moddate': datetime.datetime(2024, 3, 25, 15, 40, 25, tzinfo=datetime.timezone(datetime.timedelta(seconds=28800))), 'icv': None, 'creationdate': datetime.datetime(2024, 3, 25, 9, 32, 11, tzinfo=datetime.timezone(datetime.timedelta(se

问题: 从利润表上看，中国石油2023年的总收入、净利润分別是多少？
--------------------------------------------------------------------------------
答案: 根据中国石油天然气股份有限公司2023年度财务报表附注中的**合并综合收益表**，2023年的总收入和净利润如下：

### **总收入（营业收入）**  
**3,011,012 百万元**  
**依据文档片段**：  
在“合并综合收益表”中，营业收入（“营业收入”行）明确列示为 **3,011,012 人民币百万元**（2023年数据）。  
> 文档原文：  
> **营业收入  6  3,011,012  3,239,167**

---

### **净利润**  
**180,293 百万元**  
**依据文档片段**：  
在“合并综合收益表”中，净利润（“净利润”行）明确列示为 **180,293 人民币百万元**（2023年数据）。  
> 文档原文：  
> **净利润    180,293  163,348**

---

![](https://rean-blog-bucket.oss-cn-guangzhou.aliyuncs.com/assets/essay/20250801105923.png)

### **补充说明**  
1. **总收入的构成**：  
   根据附注中的“营业收入”分类，总收入由油气和新能源、炼油化工和新材料、销售、天然气销售等业务板块构成，合计为 **3,011,012 百万元**（见文档中“营业收入”部分的分项数据及合计数）。  

2. **净利润的计算逻辑**：  
   净利润是通过税前利润（237,462 百万元）减去所得税费用（57,169 百万元）得出，最终结果为 **180,293 百万元**。  

以上数据均直接来源于提供的财务报表附注，未涉及外部假设或计算。

相关文档片段数量: 5

来源 1:

公司: 中国石油（A股）[601857]

文件: 中国石油：2023年度报告.pdf

内容片段: 中国石油天然气股份有限公司 
2023 年度财务报表附注 
(除特别注明外，金额单位为人民币百万元) 
 
- 116 - 
1 公司简介 
 
中国石油天然气股份有限公司 (“本公司”)是由中国石油天然气集团公司根据
中华人民共和国(“中国”)原国家经济贸易委员会 《关于同意设立中国石油天然气股
份有限公司的复函》(国经贸企改[1999]1024 号)，将核心业务及与这些业务相关的资
产和负债进...

来源 2:

公司: 中国石油（A股）[601857]

文件: 中国石油：2023年度报告.pdf

内容片段: 中国石油天然气股份有限公司 
合并综合收益表 
截至 2023 年 12 月 31 日止年度 
(除特别注明外，金额单位为人民币百万元) 
- 213 - 
 
    附注   2023 年   2022 年 
     人民币  人民币 
              
营业收入  6  3,011,012  3,239,167 
       
经营支出       
采购、服务及其他    ...

来源 3:

公司: 中国石油（A股）[601857]

文件: 中国石油：2023年度报告.pdf

内容片段: 中国石油天然气股份有限公司 
2023 年度财务报表附注 
(除特别注明外，金额单位为人民币百万元) 
 
- 137 - 
4 主要会计政策和会计估计(续) 
 
(22) 收入确认 
 
收入是本集团日常活动中形成的，会导致股东权益增加且与股东投入资本无关
的经济利益的总流入。 
 
本集团在履行了合同中的履约义务，即在客户取得相关商品或服务的控制权时，
确认收入。 
 
合同中包含两项或多项...

In [32]:
question = "与2022年比较，Apple公司2023年业绩主要的变化是什么？"

ask_question(question)


问题: 与2022年比较，Apple公司2023年业绩主要的变化是什么？
--------------------------------------------------------------------------------
答案: 根据提供的文档片段，Apple公司2023年与2022年业绩的主要变化如下：

### 1. **核心产品线销售额变化**
   - **iPhone**：  
     2023年iPhone净销售额较2022年**下降2%（约49亿美元）**，主要受非Pro型号销量下滑影响，但部分被Pro型号的销量增长抵消。  
     **依据**：文档明确提到“iPhone net sales decreased 2% or $4.9 billion during 2023 compared to 2022 due to lower net sales of non-Pro iPhone models, partially offset by higher net sales of Pro iPhone models.”

   - **Mac**：  
     2023年Mac净销售额较2022年**下降108亿美元**，主要由于笔记本电脑销量减少。  
     **依据**：文档指出“Mac net sales decreased $10.8 billion during 2023 compared to 2022 due primarily to lower net sales of laptops.”

   - **iPad**：  
     2023年iPad净销售额较2022年**下降10亿美元**，主要因iPad mini和iPad Air销量下滑，部分被iPad 9代和10代的销量抵消。  
     **依据**：文档提到“iPad net sales decreased $1.0 billion during 2023 compared to 2022 due primarily to lower net sales of iPad mini and iPad Air, partially offset by the combined net sales of iPad 9th and 10th gen

{'query': '与2022年比较，Apple公司2023年业绩主要的变化是什么？',
 'result': '根据提供的文档片段，Apple公司2023年与2022年业绩的主要变化如下：\n\n### 1. **核心产品线销售额变化**\n   - **iPhone**：  \n     2023年iPhone净销售额较2022年**下降2%（约49亿美元）**，主要受非Pro型号销量下滑影响，但部分被Pro型号的销量增长抵消。  \n     **依据**：文档明确提到“iPhone net sales decreased 2% or $4.9 billion during 2023 compared to 2022 due to lower net sales of non-Pro iPhone models, partially offset by higher net sales of Pro iPhone models.”\n\n   - **Mac**：  \n     2023年Mac净销售额较2022年**下降108亿美元**，主要由于笔记本电脑销量减少。  \n     **依据**：文档指出“Mac net sales decreased $10.8 billion during 2023 compared to 2022 due primarily to lower net sales of laptops.”\n\n   - **iPad**：  \n     2023年iPad净销售额较2022年**下降10亿美元**，主要因iPad mini和iPad Air销量下滑，部分被iPad 9代和10代的销量抵消。  \n     **依据**：文档提到“iPad net sales decreased $1.0 billion during 2023 compared to 2022 due primarily to lower net sales of iPad mini and iPad Air, partially offset by the combined net sales of iPad 9th and 10th generation.”\n\n---\n\n### 2. **地区销售表现（2022年数据）**\n   -

In [35]:
question = "从利润表格（CONSOLIDATED STATEMENTS OF OPERATIONS），Apple公司2024年的销售额（Total Net sales）、净利润（Net income）？"

ask_question_with_company_filter(question, target_company="Apple")


问题: 从利润表格（CONSOLIDATED STATEMENTS OF OPERATIONS），Apple公司2024年的销售额（Total Net sales）、净利润（Net income）？
🎯 目标公司: Apple
--------------------------------------------------------------------------------
📋 检测到表格相关问题，关键词: ['表格', '表', '利润表', 'consolidated statements', 'operations']
✅ 将优先筛选表格类型文档
📋 表格类型筛选:
  - 表格文档: 13 个
  - 文本文档: 7 个
  ✅ 优先使用表格文档
📊 检索过滤统计:
  - 总检索文档: 20
  - 匹配 Apple: 20
  - 过滤掉其他公司: 0
  - 最终文档: 20
📋 表格类型筛选:
  - 表格文档: 13 个
  - 文本文档: 7 个
  ✅ 优先使用表格文档
📊 检索过滤统计:
  - 总检索文档: 20
  - 匹配 Apple: 20
  - 过滤掉其他公司: 0
  - 最终文档: 20

答案: 根据提供的文档内容，苹果公司2024年的**Total Net Sales**（总销售额）和**Net Income**（净利润）信息如下：

---

### **1. Total Net Sales（总销售额）**
**文档依据**：  
- **文档7** 提供了按类别划分的销售额数据，其中明确列示了 **Total net sales**（总销售额）为 **$391,035百万**（即3910.35亿美元）。  
  - **2024年数据**：$391,035百万  
  - **2023年数据**：$383,285百万  
  - **2022年数据**：$394,328百万  

**表格片段**：  
| 项目               | 2024       | Change | 2023       | Change | 2022       |
|--------------------|------------|--------|------------|--------|---------

{'result': '根据提供的文档内容，苹果公司2024年的**Total Net Sales**（总销售额）和**Net Income**（净利润）信息如下：\n\n---\n\n### **1. Total Net Sales（总销售额）**\n**文档依据**：  \n- **文档7** 提供了按类别划分的销售额数据，其中明确列示了 **Total net sales**（总销售额）为 **$391,035百万**（即3910.35亿美元）。  \n  - **2024年数据**：$391,035百万  \n  - **2023年数据**：$383,285百万  \n  - **2022年数据**：$394,328百万  \n\n**表格片段**：  \n| 项目               | 2024       | Change | 2023       | Change | 2022       |\n|--------------------|------------|--------|------------|--------|------------|\n| **Total net sales**| $391,035   | 2%     | $383,285   | (3)%   | $394,328   |\n\n---\n\n### **2. Net Income（净利润）**\n**文档依据**：  \n- **文档中未直接提供2024年的净利润（Net Income）数据**。  \n  - **文档1、2、3、4、5、6、8** 中均未明确列出净利润数值。  \n  - **文档7** 仅提供了销售额（Total Net Sales）和各业务线的销售额，但未涉及净利润。  \n  - **文档4** 提供了运营费用（Total operating expenses）和研发费用等，但未提及最终的净利润。  \n\n**结论**：  \n由于提供的文档中**缺乏2024年净利润的具体数值或计算依据**，无法准确回答该问题。\n\n---\n\n### **最终答案**\n- **2024年Total Net Sales**：**$391,035百万**（依据文档7）。  \n- **2024年Net Income**：**文档中未提供

In [72]:
question = "从合并资产负债表看，2023年中国移动的流动比率是多少？"
ask_question_with_company_filter(question, target_company="中国移动")


问题: 从合并资产负债表看，2023年中国移动的流动比率是多少？
🎯 目标公司: 中国移动
--------------------------------------------------------------------------------
📋 检测到表格相关问题，关键词: ['表', '资产负债表', '合并资产负债表']
✅ 将优先筛选表格类型文档
📋 表格类型筛选:
  - 表格文档: 2 个
  - 文本文档: 18 个
  ✅ 优先使用表格文档
📊 检索过滤统计:
  - 总检索文档: 20
  - 匹配 中国移动: 20
  - 过滤掉其他公司: 0
  - 最终文档: 20
📋 表格类型筛选:
  - 表格文档: 2 个
  - 文本文档: 18 个
  ✅ 优先使用表格文档
📊 检索过滤统计:
  - 总检索文档: 20
  - 匹配 中国移动: 20
  - 过滤掉其他公司: 0
  - 最终文档: 20

答案: 根据提供的文档内容，无法计算2023年中国移动的流动比率。原因如下：

1. **流动比率定义**：流动比率=流动资产/流动负债，需要合并资产负债表中具体的流动资产和流动负债数值。

2. **文档信息缺失**：
   - 文档1、文档2仅列出合并资产负债表和利润表的负责人信息，未提供具体财务数据（如流动资产、流动负债的金额）。
   - 文档3-文档8的附注部分涉及合同资产、其他流动资产、资本管理、金融工具风险等，但未披露合并资产负债表中流动资产和流动负债的量化数据。
   - 文档4提到资产负债率（总负债/总资产），但未提供流动负债的具体数值。
   - 文档8的现金流量表补充资料仅涉及现金及现金等价物的变动，未明确流动资产和流动负债的结构。

3. **关键数据缺失**：所有提供的文档片段均未包含合并资产负债表中流动资产（如货币资金、应收账款、存货等）和流动负债（如短期借款、应付账款等）的具体金额，因此无法计算流动比率。

**结论**：文档中缺乏必要的财务数据（流动资产和流动负债的数值），无法确定2023年中国移动的流动比率。建议查阅完整的合并资产负债表或相关财务报告的详细数据部分。

📄 最终使用文档数量: 8

来源 1:
  公司: 中国移动（A股）[600941]
  文件: 中国移动：2023年度报告.p

{'result': '根据提供的文档内容，无法计算2023年中国移动的流动比率。原因如下：\n\n1. **流动比率定义**：流动比率=流动资产/流动负债，需要合并资产负债表中具体的流动资产和流动负债数值。\n\n2. **文档信息缺失**：\n   - 文档1、文档2仅列出合并资产负债表和利润表的负责人信息，未提供具体财务数据（如流动资产、流动负债的金额）。\n   - 文档3-文档8的附注部分涉及合同资产、其他流动资产、资本管理、金融工具风险等，但未披露合并资产负债表中流动资产和流动负债的量化数据。\n   - 文档4提到资产负债率（总负债/总资产），但未提供流动负债的具体数值。\n   - 文档8的现金流量表补充资料仅涉及现金及现金等价物的变动，未明确流动资产和流动负债的结构。\n\n3. **关键数据缺失**：所有提供的文档片段均未包含合并资产负债表中流动资产（如货币资金、应收账款、存货等）和流动负债（如短期借款、应付账款等）的具体金额，因此无法计算流动比率。\n\n**结论**：文档中缺乏必要的财务数据（流动资产和流动负债的数值），无法确定2023年中国移动的流动比率。建议查阅完整的合并资产负债表或相关财务报告的详细数据部分。',
 'source_documents': [Document(metadata={'file': '中国移动：2023年度报告.pdf', 'company': '中国移动（A股）[600941]', 'table_count': 1.0, 'block_indices': [3], 'page_number': 95.0, 'element_type': 'table_html'}, page_content='合并资产负债表2023年12月31日(除特别注明外，金额单位为人民币百万元)\n\n[财务数据表]\n杨杰 | 李荣华 | 陈静\n企业负责人 | 主管会计工作负责人 | 会计机构负责人\n\n<table><tr><td>杨杰</td><td>李荣华</td><td>陈静</td></tr><tr><td>企业负责人</td><td>主管会计工作负责人</td><td>会计机构负责人</td></tr></table>'),
  Document(metadata={'file': '中国移动：2023年度报告.p

In [54]:
# 测试优化后的表格查询 - 简化版本
question = "从合并资产负债表看，2023年中国移动的流动资产和流动负债分别是多少？"
result = ask_question_with_company_filter(question, target_company="中国移动")

print(f"\n📊 答案摘要: {result['result'][:500]}...")
print(f"\n📄 找到的文档数量: {len(result['source_documents'])}")

# 检查找到的文档类型
for i, doc in enumerate(result['source_documents'][:3]):
    print(f"\n文档 {i+1}:")
    print(f"  文件: {doc.metadata.get('file', 'Unknown')}")
    print(f"  类型: {doc.metadata.get('element_type', 'Unknown')}")
    print(f"  内容前100字符: {doc.page_content[:100]}...")


问题: 从合并资产负债表看，2023年中国移动的流动资产和流动负债分别是多少？
🎯 目标公司: 中国移动
--------------------------------------------------------------------------------
📋 检测到表格相关问题，关键词: ['表', '资产负债表', '合并资产负债表']
✅ 将优先筛选表格类型文档
📋 表格类型筛选:
  - 表格文档: 11 个
  - 文本文档: 9 个
  ✅ 优先使用表格文档
📊 检索过滤统计:
  - 总检索文档: 20
  - 匹配 中国移动: 20
  - 过滤掉其他公司: 0
  - 最终文档: 20

答案: 根据提供的文档内容，无法直接获取2023年中国移动合并资产负债表中**流动资产**和**流动负债**的明确总额。以下是详细分析：

---

### **1. 流动资产的分析**
文档中仅提供了部分资产项目的具体数值，但未明确区分流动与非流动资产：
- **货币资金**：3,645 百万元（文档5）
- **交易性金融资产**：6,326 百万元（文档5）
- **应收账款**：93 百万元（文档5）
- **债权投资**：385 百万元（文档5）

这些项目中，**货币资金、交易性金融资产、应收账款**通常属于流动资产，但文档未明确说明其他资产（如债权投资）的流动性。此外，**其他非流动金融资产**（32,365 百万元）属于非流动资产（文档5）。

**结论**：文档未提供流动资产的总额，仅能推测部分流动资产项目，但缺乏完整数据。

---

### **2. 流动负债的分析**
文档中仅提供了部分负债项目的具体数值，但同样未明确区分流动与非流动负债：
- **应付账款**：556 百万元（文档5）

**应付账款**通常属于流动负债，但文档未提供其他流动负债（如短期借款、应交税费等）的数据。

**结论**：文档未提供流动负债的总额，仅能推测部分流动负债项目，但缺乏完整数据。

---

### **3. 总资产与总负债的参考**
文档2提供了总资产和总负债的总额，但未拆分流动与非流动部分：
- **总资产**：1,957,357 百万元（2023年12月31日）
- **总负债**：646,672 百万元（2023年12月31日）

*

In [56]:
# 直接查询中国移动合并资产负债表

# 使用更精确的查询词
search_query = "中国移动 合并资产负债表 流动资产 流动负债 2023"
docs = vectorstore.similarity_search(search_query, k=5)

print(f"找到 {len(docs)} 个相关文档")
for i, doc in enumerate(docs):
    print(f"\n=== 文档 {i+1} ===")
    print(f"公司: {doc.metadata.get('company', 'Unknown')}")
    print(f"文件: {doc.metadata.get('file', 'Unknown')}")
    print(f"类型: {doc.metadata.get('element_type', 'Unknown')}")
    print(f"页码: {doc.metadata.get('page_number', 'Unknown')}")
    
    # 检查是否是资产负债表
    content = doc.page_content
    if any(term in content for term in ['资产负债表', 'balance sheet', '流动资产', 'current assets']):
        print(f"✅ 可能包含资产负债表数据")
        # 只显示前300字符，避免输出过长
        print(f"内容预览: {content[:300]}...")
    else:
        print(f"❌ 可能不是资产负债表")
        print(f"内容预览: {content[:150]}...")
    print("-" * 80)

找到 5 个相关文档

=== 文档 1 ===
公司: 中国移动（A股）[600941]
文件: 中国移动：2023年度报告.pdf
类型: table_html
页码: 95.0
✅ 可能包含资产负债表数据
内容预览: 合并资产负债表2023年12月31日(除特别注明外，金额单位为人民币百万元)

=== 财务报表搜索摘要 ===
表格内容: 杨杰 李荣华 陈静 企业负责人 主管会计工作负责人 会计机构负责人
搜索关键词: 中国移动财务数据 中国移动财务报表 年度报告 annual report financial data income statement profit loss statement consolidated operations consolidated statements of operations statements of operations operations stateme...
--------------------------------------------------------------------------------

=== 文档 2 ===
公司: 中国移动（A股）[600941]
文件: 中国移动：2023年度报告.pdf
类型: text
页码: 147.0
✅ 可能包含资产负债表数据
内容预览: 中国移动有限公司

合并财务报表附注截至2023年12月31日止年度财务报表(除特别注明外，金额单位为人民币百万元)

四 合并财务报表项目附注 (续)

(7) 合同资产

于2023年12月31日及2022年12月31日，本集团合同资产均按组合计提减值准备，合同资产的预期损失率在   至   之间。

(8) 其他流动资产...
--------------------------------------------------------------------------------

=== 文档 3 ===
公司: 中国移动（A股）[600941]
文件: 中国移动：2023年度报告.pdf
类型: text
页码: 191.0
❌ 可能不是资产负债表
内容预览: 中国移动有限公司

合并财务报表附注截至2023年12月31日止年度财务报表(除特别注明外，金额单位为人民币百万元)

五 在其

In [71]:
# 测试改进的查询函数
result = ask_question_clean_format(
    "从合并资产负债表看，2023年中国移动的流动资产和流动负债分别是多少？计算流动比率。", 
    target_company="中国移动"
)


问题: 从合并资产负债表看，2023年中国移动的流动资产和流动负债分别是多少？计算流动比率。
🎯 目标公司: 中国移动
--------------------------------------------------------------------------------

答案: 根据提供的文档内容，未直接披露2023年中国移动的**流动资产**和**流动负债**的具体数值，因此无法直接计算流动比率。文档中提到的财务信息主要涉及金融工具风险、合同资产、租赁负债、公允价值估计等，但未明确列出合并资产负债表中流动资产和流动负债的总额。

### 需要补充的信息：
若需计算流动比率，需从合并资产负债表中获取以下数据：
1. **流动资产总额**（如应收账款、存货、现金及等价物等）。
2. **流动负债总额**（如应付账款、短期借款、一年内到期的非流动负债等）。

### 建议：
请查阅《中国移动2023年度报告》中完整的**合并资产负债表**部分，通常会在“合并资产负债表”章节直接列示流动资产和流动负债的金额。例如：
- **流动资产**可能包括货币资金、应收款项、合同资产、其他流动资产等。
- **流动负债**可能包括应付款项、短期借款、应付职工薪酬、一年内到期的非流动负债等。

如果文档中未包含具体数值，可能需要参考报告的其他部分或联系中国移动投资者关系部门获取完整数据。

📄 使用文档数量: 8

答案: 根据提供的文档内容，未直接披露2023年中国移动的**流动资产**和**流动负债**的具体数值，因此无法直接计算流动比率。文档中提到的财务信息主要涉及金融工具风险、合同资产、租赁负债、公允价值估计等，但未明确列出合并资产负债表中流动资产和流动负债的总额。

### 需要补充的信息：
若需计算流动比率，需从合并资产负债表中获取以下数据：
1. **流动资产总额**（如应收账款、存货、现金及等价物等）。
2. **流动负债总额**（如应付账款、短期借款、一年内到期的非流动负债等）。

### 建议：
请查阅《中国移动2023年度报告》中完整的**合并资产负债表**部分，通常会在“合并资产负债表”章节直接列示流动资产和流动负债的金额。例如：
- **流动资产**可能包括货币资金、应收款项、合同资产、其他流动资产等。
- **流动负债**可能包括应付款项、短期